Antes de cualquier cosa, debes autentificarte a través del cmd, ejecutando:<br>
earthengine authenticate <br>
y antes deberías instalar pip install earthengine-api geemap geopandas pandas

In [1]:
import ee
import geopandas as gpd
import pandas as pd
from datetime import datetime
from shapely.geometry import mapping
import json
from tqdm import tqdm
import csv

Hay que ir a 
https://console.cloud.google.com/apis/dashboard?invt=AbuKWg&project=maximal-osprey-287122
para habilitar la consulta.

In [2]:
# Inicializar Earth Engine
ee.Initialize(project='maximal-osprey-287122')  # Reemplaza con tu ID real

In [3]:
# Cargar shapefile local
shapefile_path = "C:/Users/Michael/Documents/ml_zc/gadm41_CHE_3.json/gadm41_CHE_3.json"

# Los datos de Suiza se obtuvieron en: https://data.humdata.org/dataset/whosonfirst-data-admin-che

gdf = gpd.read_file(shapefile_path)

In [4]:
gdf = gdf[['GID_3', 'NAME_3', 'geometry']].rename(columns={'GID_3': 'ADM3_PCODE', 'NAME_3': 'ADM3_ES'})

In [5]:
parroquias = gdf[['ADM3_PCODE', 'geometry']]

In [6]:
# parroquias = gdf[['ADM3_PCODE', 'geometry']]
# Solo selecciono dos filas, para reducir la carga de procesamiento

In [7]:
# parroquias = parroquias[parroquias['ADM3_PCODE'].isin(['EC050651', 'EC010951'])] #'EC050651', 

In [8]:
# parroquias = parroquias.iloc[775:]
# Ya que montalvo tiene una geometría muy pequeña, vamos a aumentar por metros
# gdf[gdf['ADM3_PCODE'] == 'EC160156']

In [9]:
# Función para convertir a EE FeatureCollection correctamente
def gdf_to_fc(tabla_geometria):
    features = []
    for _, row in tabla_geometria.iterrows():
        # Convierte la geometría a formato geojson (dict) con mapping()
        geojson_geom = mapping(row['geometry'])
        geom = ee.Geometry(geojson_geom)
        props = row.drop('geometry').to_dict()
        features.append(ee.Feature(geom, props))
    return ee.FeatureCollection(features)

In [21]:
# Definir años a procesar
years = [2022]

# Abrir el archivo en modo escritura (o append si ya existe)
with open('C:/Users/Michael/Documents/ml_zc/DatosObtenidos/suiza.csv', mode='w', newline='', encoding='utf-8') as file:
    # Crear el escritor CSV
    writer = csv.DictWriter(file, fieldnames=['ADM3_PCODE', 'Año', 'avg_rad_max'])
    
    # Escribir el encabezado (si es necesario)
    writer.writeheader()
    
    for num_fila in tqdm(range(0, parroquias.shape[0]), desc="Procesando parroquias", ncols=parroquias.shape[0]):
        
        # Obtener fila de la parroquia
        parroquia = parroquias.iloc[num_fila]
    
        # Convertir la fila (Serie) a un GeoDataFrame
        temp_gdf = gpd.GeoDataFrame([parroquia], geometry='geometry', crs=parroquias.crs)
    
        # Transformamos el objeto a formato compatible con Google Earth Engine
        polygon = gdf_to_fc(temp_gdf)

        # Extraemos el código de la parroquia para usarla luego
        name_parr = parroquia['ADM3_PCODE']

        # Mostrar parroquia en proceso
        print(name_parr)

        # Extraer VIIRS diciembre por parroquia:

        # Iterar sobre el periodo
        for year in years:
            start = ee.Date.fromYMD(year, 1, 1)  # Comienza desde el 1 de enero
            end = ee.Date.fromYMD(year, 12, 31)   # Termina el 31 de diciembre

            # Filtra la colección de imágenes por fecha y por el polígono
            viirs = ee.ImageCollection("NOAA/VIIRS/DNB/MONTHLY_V1/VCMSLCFG") \
                    .filterDate(start, end) \
                    .filterBounds(polygon) \
                    .select('avg_rad') \
                    .max()                              # Obtiene el valor máximo durante todo el año

            # Obtener los valores y añadir a la lista de resultados
            viirs_info = viirs.getInfo()  # Obtener la información de la imagen

            # Asumiendo que tienes la imagen de VIIRS 'viirs' y un polígono 'polygon'
            viirs_value = viirs.reduceRegion(
                reducer=ee.Reducer.mean(),  # Puedes usar otro reductor como max() si lo prefieres
                geometry=polygon,  # Polígono de interés (una parroquia, por ejemplo)
                scale=500  # Resolución de la imagen # EC160156 se consultó a 2000 y no hubo resultado.
            ).getInfo()  # Extrae la información a formato Python

            # Creamos un diccionario para agregarlos a la lista que se transformará
            row = {'ADM3_PCODE': name_parr, 'Año': year, 'avg_rad_max': viirs_value['avg_rad']}

            writer.writerow(row)

Procesando parroquias:   0%|                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            

CHE.1.1.1_1


Procesando parroquias:   0%|▉                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           

CHE.1.1.2_1


Procesando parroquias:   0%|█▉                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          

...

Procesando parroquias: 100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████

CHE.26.13.31_1


Procesando parroquias: 100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████

CHE.26.13.32_1


Procesando parroquias: 100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████